In [1]:
import sys
import os
sys.path.insert(0, os.path.abspath("/home/michaelshewarega/Desktop/test/arkouda"))
import arkouda as ak
import arachne as ar
import pandas as pd

    _         _                   _       
   / \   _ __| | _____  _   _  __| | __ _ 
  / _ \ | '__| |/ / _ \| | | |/ _` |/ _` |
 / ___ \| |  |   < (_) | |_| | (_| | (_| |
/_/   \_\_|  |_|\_\___/ \__,_|\__,_|\__,_|
                                          

Client Version: v2024.06.21


In [3]:
import argparse
import navis
from caveclient import CAVEclient

client = CAVEclient("minnie65_public")
client.materialize.version = 1300
nuc_df = client.materialize.query_table('proofreading_status_and_strategy')
filtered_df = nuc_df[(nuc_df["status_dendrite"] == "t") & (nuc_df["status_axon"] == "t")]
ids = filtered_df["pt_root_id"].values

In [5]:
def convert_swc_format(input_swc_data):
    # Split the input data by lines
    lines = input_swc_data.strip().split("\n")
    
    # Prepare a list to hold the converted data
    converted_lines = []
    
    # Loop through each line and convert it
    for line in lines:
        # Split each line by commas
        parts = line.split(",")
        
        if len(parts) == 7:
            # Reformat the line into space-separated values
            converted_line = " ".join(parts)
            converted_lines.append(converted_line)
    
    # Join the converted lines into a final string with line breaks
    return "\n".join(converted_lines)


def process_swc_file(file_path):
    # Read the SWC file
    with open(file_path, 'r') as file:
        swc_data = file.read()

    # Convert the SWC data to the correct format
    converted_data = convert_swc_format(swc_data)
    
    return converted_data

# for i in ids:
#     # Specify the file path
#     file_path = f'cave_data2/{i}.swc'
    
#     # Process the file and get the converted data
#     converted_swc_data = process_swc_file(file_path)
    
#     # # Optionally, print the converted data or save it to a new file
#     # print(converted_swc_data)
    
#     # If you want to save it to a new file, you can do so like this:
#     with open(f'./cave_data_converted/{i}.swc', 'w') as output_file:
#         output_file.write(converted_swc_data)


In [7]:
import os

for i in ids:
    # Specify the file path
    file_path = f'cave_data2/{i}.swc'
    
    # Check if the file exists before processing
    if not os.path.exists(file_path):
        print(f"File {file_path} does not exist, skipping...")
        continue  # Skip this iteration if the file does not exist
    
    # Process the file and get the converted data
    converted_swc_data = process_swc_file(file_path)
    
    # Split the converted data into lines
    converted_lines = converted_swc_data.splitlines()
    
    # Remove the first line
    converted_lines = converted_lines[1:]
    
    # Join the remaining lines back into a single string
    converted_swc_data_no_header = '\n'.join(converted_lines)
    
    # Save it to a new file
    with open(f'./cave_data_converted/{i}.swc', 'w') as output_file:
        output_file.write(converted_swc_data_no_header)


In [4]:
import navis
import arkouda
n = navis.read_swc('/home/michaelshewarega/Desktop/test/104_proofread_neurons_swc/scaled11.swc')

In [8]:
n.nodes

node_id label            x           y           z  radius  parent_id  \
0           0     1  1196.352051  492.735992  919.559998   6.146         -1   
1           1     3  1198.215942  502.864014  916.080017   0.515          0   
2           2     3  1197.488037  503.384003  916.039978   0.515          1   
3           3     3  1196.160034  504.559998  915.960022   0.515          2   
4           4     3  1196.160034  506.015991  916.440002   0.515          3   
...       ...   ...          ...         ...         ...     ...        ...   
7162     7162     3  1190.239990  501.503998  963.239990   0.071       5811   
7163     7163     3  1187.839966  502.552002  964.520020   0.072       5811   
7164     7164     3  1187.119995  502.928009  964.919983   0.072       7163   
7165     7165     3  1202.712036  493.303986  914.400024   0.052          0   
7166     7166     3  1202.807983  495.272003  914.280029   0.052       7165   

      type  
0     root  
1     slab  
2     slab  
3     slab  
4     slab  
...    ...  
7162   end  
7163  slab  
7164   end  
7165  slab  
7166   end  

[7167 rows x 8 columns]

In [20]:
# npd = navis.downsample_neuron(n, downsampling_factor=float('inf'), inplace=False)
nh = navis.heal_skeleton(n, inplace=True)
npp = navis.prune_twigs(nh, 1000, recursive= True)
npd = navis.downsample_neuron(npp, downsampling_factor=10000000, inplace=False)

In [55]:
import networkx as nx
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from matplotlib.colors import to_hex
import random

def get_random_hex_color(existing_colors=None, min_diff=50):
    if existing_colors is None:
        existing_colors = []

    def color_diff(color1, color2):
        r1, g1, b1 = (color1 >> 16) & 0xFF, (color1 >> 8) & 0xFF, color1 & 0xFF
        r2, g2, b2 = (color2 >> 16) & 0xFF, (color2 >> 8) & 0xFF, color2 & 0xFF
        return abs(r1 - r2) + abs(g1 - g2) + abs(b1 - b2)

    while True:
        color = random.randint(0, 0xFFFFFF)
        if all(color_diff(color, existing_color) >= min_diff for existing_color in existing_colors):
            existing_colors.append(color)
            return "#{:06x}".format(color)


# Create an empty list to hold new edges
new_edges = []

# Create an empty dictionary to store the node-color mappings
node_colors = {}

# Define a color map with a much larger range of distinct colors
num_colors = 500  # Number of unique colors
# color_map = cm.get_cmap('tab20', num_colors)  # You can use different colormaps (e.g., 'tab20', 'hsv', etc.)

# Loop through edges in npd.edges
# color_idx = 0  # Color index to assign different colors to nodes
# color = random.randrange(0, 1000)
# hex_color = get_random_hex_color()
for idx in npd.edges:
    nx_display = nx.Graph()
    nx_display.add_edges_from(n.edges)  # Add edges to nx_display (ensure 'n' is defined)
    
    # Find the shortest path between idx[0] and idx[1] using the 'weight' attribute
    shortest_path = nx.shortest_path(nx_display, source=idx[0], target=idx[1], weight='weight')
    # print(color_idx)
    # Vectorized approach: Assigning colors to nodes in the shortest path
    hex_color = get_random_hex_color()
    for node in shortest_path:
        if node not in node_colors:
            # Convert RGBA color to hex code
            # rgba_color = color_map(color_idx / num_colors)  # Get RGBA color
            # hex_color = to_hex(rgba_color)  # Convert to hex code
            node_colors[node] = hex_color
    # color_idx += 10

    # Optionally, you could add the path to new_edges or modify it based on your needs
    new_edges.append(shortest_path)

# Now node_colors contains a mapping of node IDs to hex color codes
# print(node_colors)


In [56]:
new_edges=[]
for idx in npd.edges:
    nx_display = nx.Graph()
    nx_display.add_edges_from(n.edges)
    shortest_path = nx.shortest_path(nx_display, source=idx[0], target=idx[1], weight='weight')
    new_edges.extend(shortest_path)

In [45]:
import json
import numpy as np

# Assuming node_colors is your dictionary with numpy.int64 keys
# Convert numpy.int64 keys to regular Python int
node_colors_converted = {int(k): v for k, v in node_colors.items()}

with open('./my_dict.json', 'w') as f:
    json.dump(node_colors_converted, f)


In [57]:
from skelescope2.src.skelescope2 import Skelescope2
# high = list(npd.nodes["node_id"].values)
viewer = Skelescope2()
viewer.testt(new_edges, node_colors, 'yes', [])
# viewer.testt([], {}, 'no', [[1189.592, 476.088, 971.56],
#  [1210.464, 612.032, 878.4],
#  [1235.776, 552.448, 763.76],
#  [1169.632, 698.504, 997.8],
#  [1165.568, 537.36, 880.4],
#  [1296.136, 522.04, 883.12],
#  [1305.232, 397.144, 858.84],
#  [1184.448, 379.408, 1004.36],
#  [1241.376, 771.528, 837.68],
#  [1303.032, 747.0, 734.88],
#  [1179.032, 491.128, 982.96],
#  [1172.48, 445.664, 882.68],
#  [1187.472, 442.432, 994.52]])
# viewer.testt()
viewer

/home/michaelshewarega/miniconda3/envs/arkouda/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning: Message serialization failed with:
keys must be str, int, float, bool or None, not numpy.int64
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant
  content = self.pack(content)


Skelescope2(decc='yes', neuronss=[{'swcText': '# ORIGINAL_SOURCE Osteoid 0.3.0\n# CREATURE \n# REGION\n# FIELD…

In [9]:
import argparse
import navis
from caveclient import CAVEclient

client = CAVEclient("minnie65_public")
client.materialize.version = 1300
nuc_df = client.materialize.query_table('proofreading_status_and_strategy')
filtered_df = nuc_df[(nuc_df["status_dendrite"] == "t") & (nuc_df["status_axon"] == "t")]
ids = filtered_df["pt_root_id"].values
synapse_table_name = client.info.get_datastack_info()["synapse_table"]
syn_proof_only_df = client.materialize.query_table(synapse_table_name, desired_resolution=[1, 1, 1], split_positions=True,
                                                   filter_in_dict={"pre_pt_root_id": ids, 
                                                                   "post_pt_root_id": ids})

# remove autapses
syn_proof_only_df = syn_proof_only_df[syn_proof_only_df["pre_pt_root_id"] != syn_proof_only_df["post_pt_root_id"]]
print(len(syn_proof_only_df))

In [14]:
# syn_proof_only_df = syn_proof_only_df[syn_proof_only_df["pre_pt_root_id"] != syn_proof_only_df["post_pt_root_id"]]
print(len(syn_proof_only_df), len(syn_proof_only_df[syn_proof_only_df["pre_pt_root_id"].isin() syn_proof_only_df["post_pt_root_id"]]))


156945


In [8]:
d= overalll(ids)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [9]:
dfe = pd.DataFrame(d)
dfe.to_csv("/home/michaelshewarega/Desktop/test/cave_new_ds_unidirection.csv", index=False)

In [17]:
df = pd.read_csv("/home/michaelshewarega/Desktop/test/cave_new_ds_unidirection.csv")
df2 = pd.read_csv("/home/michaelshewarega/Desktop/test/cave_new_ds_3.csv")
print(len(df[df["connection_type"] == 'n']), len(df2[df2["connection_type"] == 'n']))

/tmp/ipykernel_882017/4044990387.py:1: DtypeWarning: Columns (26) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("/home/michaelshewarega/Desktop/test/cave_new_ds_unidirection.csv")


501846 250923


/tmp/ipykernel_882017/4044990387.py:2: DtypeWarning: Columns (26) have mixed types. Specify dtype option on import or set low_memory=False.
  df2 = pd.read_csv("/home/michaelshewarega/Desktop/test/cave_new_ds_3.csv")
